NOTES

*   Original notebook from [Thin-Plate Spline-Motion-Model](https://colab.research.google.com/drive/1DREfdpnaBhqISg0fuQlAAIwyGVn1loH_?usp=sharing)
*   Process the selected videos from the 50 videos available.
>*   Load and process the VideoMapping and ChosenVideos excel sheets that contain mappings and video selections.
>*   ChosenVideos contains videos for each -/+ OCEAN parameter.
>*   VideoMapping contain best frames that represent that video. Best frame is the closest frame to an idle body pose.
*   Use TED model with available checkpoint.
>*   We use the pretrained version hosted by the authors here. This model is trained for 100 epochs.
*   What "*predict mode*" and "*find best frame*" from the reference implementation are?
>*   Predict mode finds the best frame as the closest frame in driving video relative to the landmarks of the source video. In this work, it is done using facealignment package and convex hull of the landmarks. Frame with minimum sum of squares error is the best frame. [Code](https://github.com/yoyo-nb/Thin-Plate-Spline-Motion-Model/blob/9520e66fa5188f011b397f7de30fb5e79cdc47de/demo.py#L97)
>*   Relative mode is related to stiching the frames of the driving video. After the best frame process continues, previous frames are processed in backward fashion then reversed and stitched.
>* Similar thing can be done for body using mediapipe. [Mediapipe colab](https://colab.research.google.com/drive/1uCuA6We9T5r0WljspEHWPHXCT_2bMKUy)
>* Applied mediapipe and default pose convex hull distance in 3D to obtain best frames for each video. The results are written to the excel file and read on later executions.


In [ ]:
!git clone https://github.com/yoyo-nb/Thin-Plate-Spline-Motion-Model.git

Cloning into 'Thin-Plate-Spline-Motion-Model'...
remote: Enumerating objects: 112, done.
remote: Counting objects: 100% (62/62), done.
remote: Compressing objects: 100% (33/33), done.
remote: Total 112 (delta 41), reused 29 (delta 29), pack-reused 50
Receiving objects: 100% (112/112), 32.65 MiB | 14.39 MiB/s, done.
Resolving deltas: 100% (49/49), done.


In [ ]:
cd Thin-Plate-Spline-Motion-Model

/content/Thin-Plate-Spline-Motion-Model


In [ ]:
# Google drive authentications

# Import PyDrive and associated libraries.
# This only needs to be done once per notebook.
from pydrive.auth import GoogleAuth
from pydrive.drive import GoogleDrive
from google.colab import auth
from oauth2client.client import GoogleCredentials

# Authenticate and create the PyDrive client.
# This only needs to be done once per notebook.
auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)

In [ ]:
#!mkdir checkpoints
#!wget -c https://cloud.tsinghua.edu.cn/f/da8d61d012014b12a9e4/?dl=1 -O checkpoints/vox.pth.tar
#!wget -c https://cloud.tsinghua.edu.cn/f/483ef53650b14ac7ae70/?dl=1 -O checkpoints/ted.pth.tar
#!wget -c https://cloud.tsinghua.edu.cn/f/9ec01fa4aaef423c8c02/?dl=1 -O checkpoints/taichi.pth.tar
#!wget -c https://cloud.tsinghua.edu.cn/f/cd411b334a2e49cdb1e2/?dl=1 -O checkpoints/mgif.pth.tar

!mkdir checkpoints
import os

ted_checkpoint_file_id = "1Oy2X7DTXp8OdbMesQ6bLzJ_sR8X86DtB"
ted_checkpoint_file = drive.CreateFile({"id": ted_checkpoint_file_id})
ted_checkpoint_file.GetContentFile(os.path.join("checkpoints", "ted_pretrained.pth.tar"))

In [ ]:
# Set the paths

from google.colab import drive
drive.mount('/content/gdrive')

data_root = "/content/gdrive/My Drive/MotionTransfer"

!mkdir -p "/content/gdrive/My Drive/MotionTransfer"
!ls "/content/gdrive/My Drive/MotionTransfer"

videos_root = os.path.join(data_root, "TED-Samples-50")

# Default pose for frames to match, preferably only upper body 
default_pose_frame_path = os.path.join(data_root, "default_pose.png")
representatives_path = os.path.join(data_root, "Representatives")

!mkdir "/content/gdrive/My Drive/MotionTransfer/Representatives"

output_folder = os.path.join(data_root, "Output")
!mkdir "/content/gdrive/My Drive/MotionTransfer/Output"

excel_name = "TED_Videos"

Mounted at /content/gdrive
badFirstTry.mp4    Representatives    TED_Videos.gsheet
chosenVideos.jpeg  sinan.png	      Thin-Plate-Spline-Motion-Model-supp.pdf
Demo		   TED-Samples-50
Output		   ted-video-map.txt
mkdir: cannot create directory ‘/content/gdrive/My Drive/AydaPaper/Representatives’: File exists
mkdir: cannot create directory ‘/content/gdrive/My Drive/AydaPaper/Output’: File exists


In [ ]:
# for listing the new videos
ocean_types = ['O', 'C', 'E', 'A', 'N']
order_types = ['Min', 'Mid', 'Max']

def getVidName(ind0,ind1):
    return "" + ocean_types[ind0] + "-" + order_types[ind1] + ".mp4"

def makeVidNameList():
    names = []
    for i in range(5):
        for j in range(3):
            names.append(getVidName(i,j))
    return names

newVidList = makeVidNameList()

print(newVidList)

['O-Min.mp4', 'O-Mid.mp4', 'O-Max.mp4', 'C-Min.mp4', 'C-Mid.mp4', 'C-Max.mp4', 'E-Min.mp4', 'E-Mid.mp4', 'E-Max.mp4', 'A-Min.mp4', 'A-Mid.mp4', 'A-Max.mp4', 'N-Min.mp4', 'N-Mid.mp4', 'N-Max.mp4']


In [ ]:
import torch

# Edit common config parameters
device = torch.device('cuda:0') if torch.cuda.is_available() else "cpu"
dataset_name = 'ted' # ['vox', 'taichi', 'ted', 'mgif']

# This file controls the epochs, structure of the model
config_path = 'config/ted-384.yaml'

find_best_frame = True # when use the relative mode to animate a face, use 'find_best_frame=True' can get better quality result
show_best_frame = True
predict_mode = 'relative' # Sequences are relative to the frame with matching landmarks
use_3D = True # Using 3D landmarks provide better performance

checkpoint_path = 'checkpoints/ted_pretrained.pth.tar'
pixel = 384

In [ ]:
!pip install mediapipe

import mediapipe as mp
mp_pose = mp.solutions.pose
mp_drawing = mp.solutions.drawing_utils
mp_drawing_styles = mp.solutions.drawing_styles

# This may only be useful for compling a ffmpeg video
try:
  import imageio
  import imageio_ffmpeg
except:
  !pip install imageio_ffmpeg

import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from skimage.transform import resize
from IPython.display import display, HTML
import warnings
import sys
from scipy.spatial import ConvexHull
from tqdm import tqdm

from skimage import img_as_ubyte
import pandas as pd
import gspread
from google.auth import default
from demo import load_checkpoints, make_animation

warnings.filterwarnings("ignore")

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 33.8/33.8 MB 51.1 MB/s eta 0:00:00


In [ ]:
dims = 3 if use_3D else 2

def landmarks2Array(landmarks):
  landmark_array = []
  for l, landmark in enumerate(landmarks):
    landmark_instance = [landmark.x, landmark.y]
    if dims == 3:
      landmark_instance.append(landmark.z)
    landmark_array.append(landmark_instance)

  return np.asarray(landmark_array)

def normalize_kp(kp):
  kp = kp - kp.mean(axis=0, keepdims=True)
  area = ConvexHull(kp[:, :dims]).volume
  area = np.sqrt(area)
  kp[:, :dims] = kp[:, :dims] / area
  return kp

def extract_landmarks(frame, pose_solver):

  pose_landmarks = pose_solver.process(frame)

  # Unlikely, but pass if no pose found
  if pose_landmarks.pose_world_landmarks is None:
    return None, None

  pose_landmark_array = landmarks2Array(pose_landmarks.pose_world_landmarks.landmark \
                                        if use_3D else pose_landmarks.pose_landmarks.landmark)
  pose_landmark_array = normalize_kp(pose_landmark_array)

  return pose_landmark_array, pose_landmarks

# Can also be used for a single frame
def extract_best_frame(frame_list,
                       default_keypoints = None):
    norm = float('inf')
    best_frame_num = 0
    best_frame_keypoints = None
    best_original_keypoints = None

    with mp_pose.Pose(static_image_mode = False,
                      min_detection_confidence=0.5,
                      model_complexity=2) as pose:

      # If no default keypoints are passed, just returns the first frame
      if default_keypoints is None:
        frame_keypoints, original_keypoints = extract_landmarks(frame_list[0], pose)
        return frame_list[0], 0, original_keypoints

      for f, frame in enumerate(tqdm(frame_list)):
        frame_keypoints, original_keypoints = extract_landmarks(frame, pose)

        if frame_keypoints is None:
          continue

        new_norm = (np.abs(default_keypoints - frame_keypoints) ** 2).sum()

        if new_norm < norm:
            norm = new_norm
            best_frame_num = f
            best_frame_keypoints = frame_keypoints
            best_original_keypoints = original_keypoints

    return frame_list[best_frame_num], best_frame_num, best_original_keypoints

def process_video(video_path, default_keypoints = None):

  video = []
  reader = imageio.get_reader(video_path)
  try:
    for frame in reader:
      video.append(frame[...,:3])
  except RuntimeError:
      pass
  reader.close()

  return video, extract_best_frame(video, default_keypoints)

def display_mash(source, driving, generated=None):
    fig = plt.figure(figsize=(8 + 4 * (generated is not None), 6))

    ims = []

    for i in range(len(driving)):
        cols = [source]
        cols.append(driving[i])
        if generated is not None:
            cols.append(generated[i])
        im = plt.imshow(np.concatenate(cols, axis=1), animated=True)
        plt.axis('off')
        ims.append([im])

    ani = animation.ArtistAnimation(fig, ims, interval=50, repeat_delay=1000)
    plt.close()
    return ani

In [ ]:
# creds, _ = default()

# gc = gspread.authorize(creds)

# worksheets = gc.open(excel_name).worksheets()
# chosen_videos_table = worksheets[0].get_all_records()
# chosen_videos_table = pd.DataFrame.from_records(chosen_videos_table)
# chosen_videos_table = chosen_videos_table.drop(columns="Pers")

# chosen_video_id_list = chosen_videos_table.values.flatten().astype(np.int)
# print(chosen_video_id_list)

# all_videos_worksheet = worksheets[1]
# all_videos_table = pd.DataFrame.from_records(worksheets[1].get_all_records())

# #Example
# print(all_videos_table.loc[chosen_video_id_list[0], "Id"])

[34 47 13 11 19 28 27 26 12 42]
hU-aTB-heU0


In [ ]:
vid_dict = {}

if find_best_frame:

  default_pose_frame = imageio.imread(default_pose_frame_path)[...,:3]

  with mp_pose.Pose(static_image_mode = True,
                      min_detection_confidence=0.5,
                      model_complexity=2) as pose:
    default_landmarks_array, keypoint_result = extract_landmarks(default_pose_frame, pose)

  plt.close()
  annotated_pose = default_pose_frame.copy()
  mp_drawing.draw_landmarks(annotated_pose,
                            keypoint_result[2].pose_landmarks,
                            mp_pose.POSE_CONNECTIONS,
                            landmark_drawing_spec=mp_drawing_styles.get_default_pose_landmarks_style())
  plt.imshow(annotated_pose)
  plt.show()

  for video_id in newVidList:
    video_path = os.path.join("/content/gdrive/My Drive/2-Selected-Ones/", video_id)

    print(f"Processing video {video_path}")
    video, keypoint_result = process_video(video_path, default_landmarks_array)
    best_frame, best_frame_id, keypoints = keypoint_result
    print(f"Best frame no: {best_frame_id}.")

    # Update excel data
    vid_dict[video_id] = best_frame_id
    # cell = all_videos_worksheet.range(f'C{video_id + 2}:C{video_id + 3}')
    # cell[0].value = best_frame_id
    # all_videos_worksheet.update_cells(cell)

    if show_best_frame:
      annotated_pose = best_frame.copy()
      mp_drawing.draw_landmarks(annotated_pose,
                              keypoints.pose_landmarks,
                              mp_pose.POSE_CONNECTIONS,
                              landmark_drawing_spec=mp_drawing_styles.get_default_pose_landmarks_style())
      display(HTML(display_mash(annotated_pose, video).to_html5_video()))

      imageio.imwrite(os.path.join(representatives_path , f"{video_id}_annotated.png"),  annotated_pose)
      imageio.imwrite(os.path.join(representatives_path , f"{video_id}_representative.png"), video[best_frame_id])

Processing video /content/gdrive/My Drive/2-Selected-Ones/O-Min.mp4


100%|██████████| 163/163 [00:21<00:00,  7.48it/s]


Best frame no: 84.


Processing video /content/gdrive/My Drive/2-Selected-Ones/O-Mid.mp4


100%|██████████| 266/266 [00:38<00:00,  6.83it/s]


...

100%|██████████| 163/163 [00:25<00:00,  6.40it/s]


Best frame no: 84.


Processing video /content/gdrive/My Drive/2-Selected-Ones/N-Max.mp4


100%|██████████| 141/141 [00:21<00:00,  6.58it/s]


Best frame no: 0.


In [ ]:
print(vid_dict)

{'O-Min.mp4': 84, 'O-Mid.mp4': 33, 'O-Max.mp4': 139, 'C-Min.mp4': 85, 'C-Mid.mp4': 19, 'C-Max.mp4': 1, 'E-Min.mp4': 0, 'E-Mid.mp4': 132, 'E-Max.mp4': 3, 'A-Min.mp4': 29, 'A-Mid.mp4': 224, 'A-Max.mp4': 139, 'N-Min.mp4': 53, 'N-Mid.mp4': 84, 'N-Max.mp4': 0}


In [ ]:
inpainting, kp_detector, dense_motion_network, avd_network = load_checkpoints(config_path = config_path, checkpoint_path = checkpoint_path, device = device)

In [ ]:
def transfer_i_to_j(i,itype,j,jtype):

  video_path = os.path.join("/content/gdrive/My Drive/2-Selected-Ones/", getVidName(i,itype))
  source_video, _ = process_video(video_path, None)

  best_frame_id = vid_dict[getVidName(i,itype)] # all_videos_table.loc[source, "BestFrameNo"]

  source_image = resize(source_video[best_frame_id], (pixel, pixel))[..., :3]

  output_name = f"s{getVidName(i,itype)}_d{getVidName(j,jtype)}.mp4"

  output_path = os.path.join("/content/gdrive/My Drive/2-Selected-Ones/", output_name)

  if os.path.exists(output_path):
    print(f"Skipping {output_name} since it exists.")
  else:
    print(f"Producing {output_name}")

    video_path = os.path.join("/content/gdrive/My Drive/2-Selected-Ones/", getVidName(j,jtype))

    driving_video, _ = process_video(video_path, None)
    driving_image_index =  vid_dict[getVidName(j,jtype)] # all_videos_table.loc[driving, "BestFrameNo"]

    driving_video = [resize(frame, (pixel, pixel))[..., :3] for frame in driving_video]

    # Split the video accordingly to relative part
    predictions_forward = make_animation(source_image, driving_video[driving_image_index:], inpainting, kp_detector, dense_motion_network, avd_network, device = device, mode = predict_mode)
    predictions_backward = make_animation(source_image, driving_video[:(driving_image_index+1)][::-1], inpainting, kp_detector, dense_motion_network, avd_network, device = device, mode = predict_mode)
    predictions = predictions_backward[::-1] + predictions_forward[1:]

    imageio.mimsave(output_path, [img_as_ubyte(frame) for frame in predictions], fps=30)


In [ ]:
for i in range (5):
  # first index is appearance
  # appereance is mid
  transfer_i_to_j(i,1,i,0)
  transfer_i_to_j(i,1,i,2)

  # movement is mid
  transfer_i_to_j(i,0,i,1)
  transfer_i_to_j(i,2,i,1)

  # cross
  transfer_i_to_j(i,0,i,2)
  transfer_i_to_j(i,2,i,0)

  # appereance is min
  transfer_i_to_j(i,0,i,0)
  transfer_i_to_j(i,0,i,2)

  # appereance is max
  transfer_i_to_j(i,2,i,0)
  transfer_i_to_j(i,2,i,2)

Producing sO-Mid.mp4_dO-Min.mp4.mp4


100%|██████████| 85/85 [00:11<00:00,  7.41it/s]


Producing sO-Mid.mp4_dO-Max.mp4.mp4


100%|██████████| 140/140 [00:19<00:00,  7.21it/s]


Producing sO-Min.mp4_dO-Mid.mp4.mp4


...

100%|██████████| 54/54 [00:08<00:00,  6.48it/s]


Producing sN-Min.mp4_dN-Min.mp4.mp4


100%|██████████| 54/54 [00:08<00:00,  6.54it/s]


Skipping sN-Min.mp4_dN-Max.mp4.mp4 since it exists.
Skipping sN-Max.mp4_dN-Min.mp4.mp4 since it exists.
Producing sN-Max.mp4_dN-Max.mp4.mp4


100%|██████████| 1/1 [00:00<00:00,  6.76it/s]
